In [305]:
import sys
import os
import pandas as pd
import ollama
import json
import re

# Add the root directory to sys.path
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))

In [306]:
from configurations import AUDIO_AND_LYRICS_TABLE_NAME, AUDIO_LYRICS_AND_FEATURE_SUMAMRIZER  

In [307]:

def extract_tags_content(content, tags_list):
    """
    Extract content from specified tags and return it as a formatted string.
    
    Args:
        content (str): The input text containing tagged content
        tags_list (list): List of tag names to extract
    
    Returns:
        str: Formatted string with all extracted content
    """
    result = []
    for tag in tags_list:
        # Regex pattern that handles potential malformed XML and duplicate tags
        pattern = f"<{tag}>(.*?)</{tag}>"
        matches = re.findall(pattern, content, re.DOTALL)
        
        if matches:
            for match in matches:
                # Clean up the extracted content (remove leading/trailing whitespace)
                cleaned_content = match.strip()
                # Add the tagged content with a header to the result
                result.append(f"{cleaned_content}\n")
    
    # Join all extracted content with double line breaks for UI display
    return "\n".join(result)

In [308]:

def audio_features_to_json(df: pd.DataFrame):
    """
    Convert a DataFrame containing audio features to a JSON format suitable for LLM prompting.
    
    Parameters:
    df (pandas.DataFrame): DataFrame with columns for audio features
    
    Returns:
    str: JSON string representation of the audio features
    """
    # Ensure the DataFrame has the expected columns
    expected_columns = [
        'danceability', 'energy', 'key', 'loudness', 'mode', 
        'speechiness', 'acousticness', 'instrumentalness', 
        'liveness', 'valence', 'tempo'
    ]
    
    # Create a dictionary for each row in the DataFrame
    features_list = []
    for _, row in df.iterrows():
        # Extract features as a dictionary
        features = {}
        for col in expected_columns:
            if col in df.columns:
                features[col] = float(row[col])
            else:
                print(f"Warning: Column '{col}' not found in DataFrame")
        
        features_list.append(features)
    
    # Convert to JSON string with indentation for readability
    json_str = json.dumps(features_list, indent=2)
    return json_str

In [ ]:
from credentials import SUPABASE_URL, SUPABASE_KEY
from supabase import create_client, Client
import asyncio
from itertools import islice
import pandas as pd

key = ""

# Initialize the client
async def create_supabase_connection():
    supabase: Client = create_client("", key)
    print("Supabase connection created: ", supabase)
    return supabase

In [310]:
supabase_client = await create_supabase_connection()

Supabase connection created:  <supabase._sync.client.SyncClient object at 0x135066610>


In [311]:
async def fetch_all_data_from_table(supabase_client, table_name):
    """
    Fetch all data from a specified table in Supabase.
    
    Parameters:
    -----------
    supabase_client : Client
        An initialized Supabase client object
    table_name : str
        The name of the table to fetch data from
        
    Returns:
    --------
    dict
        A dictionary containing all the data from the table
    
    Raises:
    -------
    Exception
        If there is an error in fetching the data
    """
    try:
        # Query the table to get all rows
        response = supabase_client.table(table_name).select('*').execute()
        
        # Extract the data from the response
        data = response.data
        
        print(f"Successfully fetched {len(data)} rows from table '{table_name}'")
        return data
    
    except Exception as e:
        print(f"Error fetching data from table '{table_name}': {str(e)}")
        raise

In [312]:
df = await fetch_all_data_from_table(supabase_client,AUDIO_AND_LYRICS_TABLE_NAME)
df = pd.DataFrame(df)

Successfully fetched 4822 rows from table 'summary_lyrics_plus_features'


In [313]:
def format_prompt(lyrics, audio_features_json):
    """
    Format the prompt with the actual lyrics and audio features.
    
    Parameters:
    -----------
    lyrics (str): The song lyrics
    audio_features_json (str): JSON string of audio features
    
    Returns:
    --------
    str: The formatted prompt ready to send to the model
    """
    # Replace the placeholders with actual data
    formatted_prompt = AUDIO_LYRICS_AND_FEATURE_SUMAMRIZER.replace(
        "{{LYRICS}}", lyrics
    ).replace(
        "{{AUDIO_FEATURES}}", audio_features_json
    )
    
    return formatted_prompt

In [314]:
async def prompt_ollama_model(lyrics, audio_features):
    
    formatted_prompt = format_prompt(lyrics, audio_features)
    
    response = ollama.chat(
        model='gemma3:12b',
        messages=[
            {
                'role': 'user',
                'content': formatted_prompt
            }
        ]
    )
    print("response is: ", response['message']['content'])
    return response['message']['content']

In [ ]:
# Experiment code to perform LLM prompting via Ollama
# Apply nest_asyncio to allow nested event loops (important for Jupyter notebooks)
nest_asyncio.apply()

async def process_song_data2(df):
    """
    Process each row in the DataFrame, extract audio features, and prompt Ollama model
    with lyrics and audio features.
    """
    results = []
    
    for index, row in df.iterrows():
        try:
            print(f"Processing row {index + 1}/{len(df)}")
            
            # Extract lyrics
            lyrics = row.get('lyrics', '')
            if not lyrics or pd.isna(lyrics):
                print(f"Warning: No lyrics found for row {index}")
                continue
            
            # Create a single-row DataFrame with just the audio features from this row
            audio_features_df = pd.DataFrame([row])
            
            # Use function 2 to convert audio features to JSON
            audio_features_json = audio_features_to_json(audio_features_df)
            
            # Use function 1 to get response from Ollama
            response = await prompt_ollama_model(lyrics, audio_features_json)
            
            cleaned_response = extract_tags_content(response, ['song_description'])

            # Store result with index for reference
            results.append({
                'index': index,
                'spotify_id': row.get('spotify_id', f'unknown_{index}'),
                'name': row.get('name', f'unknown_{index}'),
                'response': cleaned_response
            })
            
            # Optional: add a delay to avoid rate limits
            await asyncio.sleep(0.5)
            
        except Exception as e:
            print(f"Error processing row {index}: {str(e)}")
            continue
    
    return results

def run_analysis2(df):
    """
    Run the async processing function and return results
    """
    try:
        # Create a new event loop explicitly
        loop = asyncio.new_event_loop()
        asyncio.set_event_loop(loop)
        results = loop.run_until_complete(process_song_data(df))
    except RuntimeError as e:
        if "This event loop is already running" in str(e):
            # If we're in a Jupyter notebook or similar environment with an existing event loop
            print("Using nest_asyncio to run with existing event loop")
            results = asyncio.run(process_song_data(df))
        else:
            raise e
    
    # Convert results to DataFrame for easier analysis
    results_df = pd.DataFrame(results)
    
    print(f"Processed {len(results_df)} songs successfully")
    return results_df

In [316]:
import pandas as pd
import json
import ollama
import asyncio
import nest_asyncio

# Apply nest_asyncio to allow nested event loops (important for Jupyter notebooks)
nest_asyncio.apply()

async def process_song_data(df):
    """
    Process each row in the DataFrame, extract audio features, and prompt Ollama model
    with lyrics and audio features.
    """
    results = []
    
    # Check if df is a list and convert it to DataFrame if needed
    if isinstance(df, list):
        df = pd.DataFrame(df)
    
    for index, row in df.iterrows():
        try:
            print(f"Processing row {index + 1}/{len(df)}")
            # Extract lyrics
            lyrics = row.get('lyrics', '')
            if not lyrics or pd.isna(lyrics):
                print(f"Warning: No lyrics found for row {index}")
                continue
                
            # Create a single-row DataFrame with just the audio features from this row
            audio_features_df = pd.DataFrame([row])
            
            # Use function 2 to convert audio features to JSON
            audio_features_json = audio_features_to_json(audio_features_df)
            
            # Use function 1 to get response from Ollama
            response = await prompt_ollama_model(lyrics, audio_features_json)
            cleaned_response = extract_tags_content(response, ['song_description'])
            
            # Store result with index for reference
            results.append({
                'index': index,
                'spotify_id': row.get('spotify_id', f'unknown_{index}'),
                'name': row.get('name', f'unknown_{index}'),
                'response': cleaned_response
            })
            
            # Optional: add a delay to avoid rate limits
            await asyncio.sleep(0.5)
        except Exception as e:
            print(f"Error processing row {index}: {str(e)}")
            continue
            
    return results

def run_analysis(df):
    """
    Run the async processing function and return results
    """
    # Check if df is a list and convert it to DataFrame if needed
    if isinstance(df, list):
        df = pd.DataFrame(df)
        
    try:
        # Create a new event loop explicitly
        loop = asyncio.new_event_loop()
        asyncio.set_event_loop(loop)
        results = loop.run_until_complete(process_song_data(df))
    except RuntimeError as e:
        if "This event loop is already running" in str(e):
            # If we're in a Jupyter notebook or similar environment with an existing event loop
            print("Using nest_asyncio to run with existing event loop")
            results = asyncio.run(process_song_data(df))
        else:
            raise e
            
    # Convert results to DataFrame for easier analysis
    results_df = pd.DataFrame(results)
    print(f"Processed {len(results_df)} songs successfully")
    return results_df


In [317]:
results = run_analysis(df)

Processing row 1/4822
response is:  <song_description>
This song portrays a complex and turbulent relationship, grappling with the push and pull of deep affection and underlying frustration. The narrative suggests a cyclical pattern of near-separation and reluctant reconciliation, hinting at a bittersweet dependency between two individuals seemingly destined to orbit each other. The lyrics convey a sense of inevitability and a quiet resignation to a pattern neither party can fully break. It's a contemplation on the bittersweet nature of love, acknowledging its capacity for both immense joy and profound pain.

Musically, the track possesses a contemplative and somewhat melancholic atmosphere. While the tempo is moderate, lending itself to a relaxed feel, the danceability suggests a subtle groove that prevents it from being overly somber. The energy level is restrained, mirroring the introspective nature of the lyrics. Its acoustic nature and moderate loudness contribute to an intimate a

In [318]:
results

index              spotify_id                 name  \
0         0  4tNXntkAzQ5A2dfYRYGIIQ               Easier   
1         1  4wBcaYqLPm7EtDVoJQORU4              Bust Me   
2         2  3PzeZR8CqtwXmSn5AVao7J                DEATH   
3         3  4wdZdkEugVVorAfzqRqC6N          Candy Paint   
4         4  4yI3HpbSFSgFZtJP2kDe5m      Look At Her Now   
...     ...                     ...                  ...   
4816   4817  5JdLUE9D743ob2RtgmVpVx               Makeba   
4817   4818  5KVciTEfXvpcFHR3RFbtJy               Wassup   
4818   4819  5KW4KhJIAbVVSH6pJ4GPkb       Tie That Binds   
4819   4820  5Lgqu1th1KqlG97OF2gWGe  Window Pain - Outro   
4820   4821  5NU40QTlXrDUJzDBdv79bg          Deserve You   

                                               response  
0     This song portrays a complex and turbulent rel...  
1     This track pulses with a confident and swagger...  
2     This song explores themes of mortality, loss, ...  
3     This track exudes a confident and assertive sw...  
4     This song tells a story of heartbreak and even...  
...                                                 ...  
4816  This track evokes a feeling of joyous celebrat...  
4817  This track presents a confident and assertive ...  
4818  This track conveys a deep sense of longing and...  
4819  This emotionally charged track navigates theme...  
4820  This song explores a deep sense of self-doubt ...  

[4821 rows x 4 columns]

In [319]:
results.to_csv('final_song_summary.csv')

In [320]:
results

index              spotify_id                 name  \
0         0  4tNXntkAzQ5A2dfYRYGIIQ               Easier   
1         1  4wBcaYqLPm7EtDVoJQORU4              Bust Me   
2         2  3PzeZR8CqtwXmSn5AVao7J                DEATH   
3         3  4wdZdkEugVVorAfzqRqC6N          Candy Paint   
4         4  4yI3HpbSFSgFZtJP2kDe5m      Look At Her Now   
...     ...                     ...                  ...   
4816   4817  5JdLUE9D743ob2RtgmVpVx               Makeba   
4817   4818  5KVciTEfXvpcFHR3RFbtJy               Wassup   
4818   4819  5KW4KhJIAbVVSH6pJ4GPkb       Tie That Binds   
4819   4820  5Lgqu1th1KqlG97OF2gWGe  Window Pain - Outro   
4820   4821  5NU40QTlXrDUJzDBdv79bg          Deserve You   

                                               response  
0     This song portrays a complex and turbulent rel...  
1     This track pulses with a confident and swagger...  
2     This song explores themes of mortality, loss, ...  
3     This track exudes a confident and assertive sw...  
4     This song tells a story of heartbreak and even...  
...                                                 ...  
4816  This track evokes a feeling of joyous celebrat...  
4817  This track presents a confident and assertive ...  
4818  This track conveys a deep sense of longing and...  
4819  This emotionally charged track navigates theme...  
4820  This song explores a deep sense of self-doubt ...  

[4821 rows x 4 columns]

In [324]:
# Now update each row in the table, matching by spotify_id
success_count = 0
for index, row in results.iterrows():
    try:
        # Get the spotify_id and response for this row
        spotify_id = row['spotify_id']
        response_value = row['response']
        
        # Update the Supabase table
        result = supabase_client.table(AUDIO_AND_LYRICS_TABLE_NAME).update(
            {"lyrics_audio_features_summary": response_value}
        ).eq("spotify_id", spotify_id).execute()
        
        success_count += 1
    except Exception as e:
        print(f"Error updating row with spotify_id {spotify_id}: {str(e)}")

print(f"Successfully updated {success_count} rows in the Supabase table with response values")

Successfully updated 4821 rows in the Supabase table with response values
